In [ ]:
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [ ]:
!pip install fasttext

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.4/73.4 kB 2.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Using cached pybind11-2.13.6-py3-none-any.whl.metadata (9.5 kB)
Using cached pybind11-2.13.6-py3-none-any.whl (243 kB)
  Created wheel for fasttext: filename=fasttext-0.9.3-cp310-cp310-linux_x86_64.whl size=4296185 sha256=ce06dd35bee0c9d8244e7fb1de5eb58b6c68599b0ed15c0ac30c6905443246b0
  Stored in directory: /root/.cache/pip/wheels/0d/a2/00/81db54d3e6a8199b829d58e02cec2ddb20ce3e59fad8d3c92a
Successfully built fasttext


In [ ]:
!pip install lazypredict

In [ ]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.model_selection import train_test_split, KFold
import fasttext
from lazypredict.Supervised import LazyClassifier
from transformers import BertTokenizer
import gensim
import gensim.downloader

dataset = pd.read_excel("/content/drive/MyDrive/domain/Synthetic User Stories.xlsx")
dataset

/usr/local/lib/python3.10/dist-packages/dask/dataframe/__init__.py:42: FutureWarning: 
Dask dataframe query planning is disabled because dask-expr is not installed.

You can install it with `pip install dask[dataframe]` or `conda install dask`.
This will raise in a future version.

  warnings.warn(msg, FutureWarning)


Domain      Machine Learning Task  \
0                Biology  abstractive summarization   
1          Plant Science  abstractive summarization   
2                Biology      action model learning   
3          Plant Science      action model learning   
4                Biology        activation function   
...                  ...                        ...   
12396    Computer Vision  word-sense disambiguation   
12397  Computer Networks                   word2vec   
12398    Computer Vision                   word2vec   
12399  Computer Networks                    wordnet   
12400    Computer Vision                    wordnet   

                                              User Story  
0      A group of researchers is using abstractive su...  
1      As a plant scientist, I want to use abstractiv...  
2      As a molecular biologist, I want to use action...  
3      As a plant scientist, I want to use action mod...  
4      As a bioinformatics researcher, I want to use ...  
...                                                  ...  
12396  As a computer vision researcher, I want to use...  
12397  As a network engineer, I want to use word2vec ...  
12398  As a computer vision researcher, I want to use...  
12399  As a network engineer, I want to use WordNet t...  
12400  As a computer vision researcher, I want to use...  

[12401 rows x 3 columns]

In [ ]:
target = []
for row in dataset.iterrows():
    target.append(np.where(dataset["Domain"].unique() == row[1]["Domain"])[0][0])
dataset["Target"] = target
dataset["Target"]

0         0
1         1
2         0
3         1
4         0
         ..
12396    37
12397    36
12398    37
12399    36
12400    37
Name: Target, Length: 12401, dtype: int64

In [ ]:
from transformers import RobertaTokenizer
from transformers import AlbertTokenizer
from transformers import DistilBertTokenizer

In [ ]:
def getTrainSetFastText():
    ft_model = fasttext.load_model("fasttext_model.bin")
    traindata = []
    for msg in dataset['User Story']:
        traindata.append(ft_model.get_sentence_vector(msg))
    traindata = pd.DataFrame(traindata)
    traindata.columns = traindata.columns.astype(str)
    return traindata

def getTrainSetTFIDF():
    countvec = CountVectorizer(max_features=100)
    bow = countvec.fit_transform(dataset['User Story']).toarray()
    tfidfconverter = TfidfTransformer()
    X = tfidfconverter.fit_transform(bow).toarray()
    training_data = pd.DataFrame(X)
    training_data.columns = training_data.columns.astype(str)
    return training_data

def getTrainSetBERT():
    tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
    tokenized_data = tokenizer(dataset['User Story'].tolist(), padding=True, truncation=True, max_length=100)
    traindata = []
    for msg in tokenized_data['input_ids']:
        traindata.append(msg)
    traindata = pd.DataFrame(traindata)
    traindata.columns = traindata.columns.astype(str)
    return traindata

def getTrainSetRoBERTa():
    tokenizer = RobertaTokenizer.from_pretrained('roberta-base')
    tokenized_data = tokenizer(dataset['User Story'].tolist(), padding=True, truncation=True, max_length=100)
    traindata = []
    for msg in tokenized_data['input_ids']:
        traindata.append(msg)
    traindata = pd.DataFrame(traindata)
    traindata.columns = traindata.columns.astype(str)
    return traindata

def getTrainSetALBERT():
    tokenizer = AlbertTokenizer.from_pretrained('albert-base-v2')
    tokenized_data = tokenizer(dataset['User Story'].tolist(), padding=True, truncation=True, max_length=100)
    traindata = []
    for msg in tokenized_data['input_ids']:
        traindata.append(msg)
    traindata = pd.DataFrame(traindata)
    traindata.columns = traindata.columns.astype(str)
    return traindata

def getTrainSetDistilBERT():
    tokenizer = DistilBertTokenizer.from_pretrained('distilbert-base-uncased')
    tokenized_data = tokenizer(dataset['User Story'].tolist(), padding=True, truncation=True, max_length=100)
    traindata = []
    for msg in tokenized_data['input_ids']:
        traindata.append(msg)
    traindata = pd.DataFrame(traindata)
    traindata.columns = traindata.columns.astype(str)
    return traindata

def getTrainSetWord2Vec():
    w2v_model = gensim.models.KeyedVectors.load_word2vec_format('word2vec-google-news-300.bin', binary=True)
    traindata = []
    for msg in dataset['User Story']:
        words = msg.split()
        vecs = []
        for word in words:
            if word in w2v_model:
                vecs.append(w2v_model[word][:100])
        if vecs:
            vec_avg = sum(vecs) / len(vecs)
        else:
            vec_avg = [0] * 100
        traindata.append(vec_avg)

    traindata = pd.DataFrame(traindata)
    traindata.columns = traindata.columns.astype(str)
    return traindata

def getTrainSetGlove():
    glove_vectors = gensim.downloader.load('glove-wiki-gigaword-100')
    traindata = []
    for msg in dataset['User Story']:
        words = msg.split()
        vecs = []
        for word in words:
            if word in glove_vectors:
                vecs.append(glove_vectors[word])
        if vecs:
            vec_avg = sum(vecs) / len(vecs)
        else:
            vec_avg = [0] * 100
        traindata.append(vec_avg)

    traindata = pd.DataFrame(traindata)
    traindata.columns = traindata.columns.astype(str)
    return traindata

In [ ]:
X = getTrainSetGlove() #Change this to get training set based on word embeddings method.
y = dataset['Target']
X_train, X_test, y_train, y_test = train_test_split(X, y,test_size=.5,random_state =123)
clf = LazyClassifier(verbose=0,ignore_warnings=True, custom_metric=None)
models,predictions = clf.fit(X_train, X_test, y_train, y_test)
models

[==================================================] 100.0% 128.1/128.1MB downloaded


 97%|█████████▋| 30/31 [02:14<00:10, 10.16s/it]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.009249 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 25500
[LightGBM] [Info] Number of data points in the train set: 6200, number of used features: 100
[LightGBM] [Info] Start training from score -3.495863
[LightGBM] [Info] Start training from score -3.495863
[LightGBM] [Info] Start training from score -3.517369
[LightGBM] [Info] Start training from score -3.539348
[LightGBM] [Info] Start training from score -3.561821
[LightGBM] [Info] Start training from score -3.544919
[LightGBM] [Info] Start training from score -3.596506
[LightGBM] [Info] Start training from score -3.561821
[LightGBM] [Info] Start training from score -3.469614
[LightGBM] [Info] Start training from score -3.556155
[LightGBM] [Info] Start training from score -3.533808
[LightGBM] [Info] Start training from score -3.517369
[LightGBM] [Info] Start training from score -3.556155
[LightGB

100%|██████████| 31/31 [02:41<00:00,  5.21s/it]


Accuracy  Balanced Accuracy ROC AUC  F1 Score  \
Model                                                                        
LinearDiscriminantAnalysis       0.90               0.82    None      0.90   
LogisticRegression               0.90               0.81    None      0.90   
LinearSVC                        0.89               0.81    None      0.89   
CalibratedClassifierCV           0.90               0.80    None      0.90   
SVC                              0.88               0.79    None      0.88   
RidgeClassifier                  0.87               0.78    None      0.87   
RidgeClassifierCV                0.87               0.78    None      0.87   
PassiveAggressiveClassifier      0.87               0.78    None      0.87   
SGDClassifier                    0.85               0.76    None      0.86   
Perceptron                       0.84               0.76    None      0.85   
NearestCentroid                  0.78               0.72    None      0.78   
XGBClassifier                    0.80               0.72    None      0.80   
GaussianNB                       0.78               0.70    None      0.78   
RandomForestClassifier           0.77               0.69    None      0.77   
ExtraTreesClassifier             0.75               0.68    None      0.75   
BernoulliNB                      0.75               0.67    None      0.75   
KNeighborsClassifier             0.66               0.59    None      0.66   
BaggingClassifier                0.61               0.55    None      0.61   
DecisionTreeClassifier           0.44               0.39    None      0.44   
ExtraTreeClassifier              0.32               0.32    None      0.33   
LGBMClassifier                   0.19               0.17    None      0.16   
AdaBoostClassifier               0.09               0.08    None      0.05   
LabelSpreading                   0.04               0.04    None      0.02   
LabelPropagation                 0.04               0.04    None      0.02   
DummyClassifier                  0.03               0.03    None      0.00   

                             Time Taken  
Model                                    
LinearDiscriminantAnalysis         0.49  
LogisticRegression                 1.21  
LinearSVC                          4.00  
CalibratedClassifierCV            16.62  
SVC                                8.07  
RidgeClassifier                    0.11  
RidgeClassifierCV                  0.32  
PassiveAggressiveClassifier        1.33  
SGDClassifier                      4.67  
Perceptron                         0.91  
NearestCentroid                    0.09  
XGBClassifier                     43.90  
GaussianNB                         0.20  
RandomForestClassifier            13.34  
ExtraTreesClassifier               2.97  
BernoulliNB                        0.18  
KNeighborsClassifier               0.80  
BaggingClassifier                 13.73  
DecisionTreeClassifier             2.00  
ExtraTreeClassifier                0.07  
LGBMClassifier                    27.20  
AdaBoostClassifier                 9.72  
LabelSpreading                     6.69  
LabelPropagation                   2.45  
DummyClassifier                    0.05

In [ ]:
models[["Accuracy","F1 Score"]][:10]

In [ ]:
result = pd.DataFrame(columns=["Fold","Model","Accuracy","F1-Score"], index=np.arange(300))
fold = KFold(n_splits=10, random_state=6666, shuffle=True)
X = getTrainSetWord2Vec() #Change this to get training set based on word embeddings method.
y = dataset['Target']
counter = 0
foldcounter = 1
for train_index, test_index in fold.split(X, y):
        print("Processing Fold "+ str(foldcounter) + " ...")
        X_train, X_test, y_train, y_test = \
            X[ X.index.isin(train_index)], X[ X.index.isin(test_index)], y[train_index], y[test_index]
        clf = LazyClassifier(verbose=0,ignore_warnings=True, custom_metric=None)
        models,predictions = clf.fit(X_train, X_test, y_train, y_test)
        for model in models[:].iterrows():
            result.loc[counter]["Fold"] = foldcounter
            result.loc[counter]["Model"] = model[0]
            result.loc[counter]["Accuracy"] = round(model[1][0],3)
            result.loc[counter]["F1-Score"] = round(model[1][3],3)
            counter += 1
        foldcounter += 1
result

Processing Fold 1 ...


100%|██████████| 29/29 [03:42<00:00,  7.69s/it]


Processing Fold 2 ...


100%|██████████| 29/29 [03:42<00:00,  7.68s/it]


Processing Fold 3 ...


...

Processing Fold 9 ...


100%|██████████| 29/29 [03:50<00:00,  7.96s/it]


Processing Fold 10 ...


100%|██████████| 29/29 [03:53<00:00,  8.07s/it]


Fold                       Model Accuracy F1-Score
0      1                         SVC     0.90     0.90
1      1          LogisticRegression     0.90     0.90
2      1      CalibratedClassifierCV     0.89     0.89
3      1                   LinearSVC     0.89     0.89
4      1  LinearDiscriminantAnalysis     0.89     0.89
..   ...                         ...      ...      ...
295  NaN                         NaN      NaN      NaN
296  NaN                         NaN      NaN      NaN
297  NaN                         NaN      NaN      NaN
298  NaN                         NaN      NaN      NaN
299  NaN                         NaN      NaN      NaN

[300 rows x 4 columns]

In [ ]:
# for alberta the accuracy
X = getTrainSetALBERT() #Change this to get training set based on word embeddings method.
y = dataset['Target']
X_train, X_test, y_train, y_test = train_test_split(X, y,test_size=.5,random_state =123)
clf = LazyClassifier(verbose=0,ignore_warnings=True, custom_metric=None)
models,predictions = clf.fit(X_train, X_test, y_train, y_test)
models

 97%|█████████▋| 30/31 [15:22<00:05,  5.25s/it]

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002903 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 11219
[LightGBM] [Info] Number of data points in the train set: 6200, number of used features: 76
[LightGBM] [Info] Start training from score -3.495863
[LightGBM] [Info] Start training from score -3.495863
[LightGBM] [Info] Start training from score -3.517369
[LightGBM] [Info] Start training from score -3.539348
[LightGBM] [Info] Start training from score -3.561821
[LightGBM] [Info] Start training from score -3.544919
[LightGBM] [Info] Start training from score -3.596506
[LightGBM] [Info] Start training from score -3.561821
[LightGBM] [Info] Start training from score -3.469614
[LightGBM] [Info] Start training from score -3.556155
[LightGBM] [Info] Start training from score -3.533808
[LightGBM] [Info] Start training from score -3.517369

100%|██████████| 31/31 [15:33<00:00, 30.13s/it]


Accuracy  Balanced Accuracy ROC AUC  F1 Score  \
Model                                                                        
XGBClassifier                    0.98               0.88    None      0.98   
BaggingClassifier                0.98               0.87    None      0.98   
DecisionTreeClassifier           0.97               0.87    None      0.97   
ExtraTreesClassifier             0.88               0.79    None      0.88   
RandomForestClassifier           0.83               0.74    None      0.82   
LogisticRegression               0.46               0.42    None      0.45   
LinearDiscriminantAnalysis       0.46               0.41    None      0.44   
ExtraTreeClassifier              0.44               0.40    None      0.45   
LinearSVC                        0.40               0.36    None      0.37   
SVC                              0.36               0.33    None      0.35   
SGDClassifier                    0.36               0.32    None      0.36   
CalibratedClassifierCV           0.35               0.31    None      0.29   
NearestCentroid                  0.29               0.26    None      0.27   
Perceptron                       0.26               0.23    None      0.25   
BernoulliNB                      0.25               0.23    None      0.24   
RidgeClassifier                  0.24               0.22    None      0.18   
RidgeClassifierCV                0.24               0.22    None      0.18   
PassiveAggressiveClassifier      0.24               0.21    None      0.23   
LabelPropagation                 0.14               0.13    None      0.14   
LabelSpreading                   0.14               0.13    None      0.14   
KNeighborsClassifier             0.14               0.13    None      0.14   
GaussianNB                       0.13               0.11    None      0.07   
AdaBoostClassifier               0.08               0.08    None      0.05   
LGBMClassifier                   0.03               0.03    None      0.01   
DummyClassifier                  0.03               0.03    None      0.00   

                             Time Taken  
Model                                    
XGBClassifier                     11.43  
BaggingClassifier                  1.54  
DecisionTreeClassifier             0.37  
ExtraTreesClassifier               2.41  
RandomForestClassifier             3.58  
LogisticRegression                 2.47  
LinearDiscriminantAnalysis         0.44  
ExtraTreeClassifier                0.12  
LinearSVC                        195.46  
SVC                               13.07  
SGDClassifier                      4.21  
CalibratedClassifierCV           667.97  
NearestCentroid                    0.10  
Perceptron                         0.93  
BernoulliNB                        0.10  
RidgeClassifier                    0.09  
RidgeClassifierCV                  0.30  
PassiveAggressiveClassifier        1.37  
LabelPropagation                   3.35  
LabelSpreading                     9.40  
KNeighborsClassifier               0.82  
GaussianNB                         0.20  
AdaBoostClassifier                 1.79  
LGBMClassifier                    11.66  
DummyClassifier                    0.07

In [ ]:
# for roberta the accuracy
X = getTrainSetRoBERTa() #Change this to get training set based on word embeddings method.
y = dataset['Target']
X_train, X_test, y_train, y_test = train_test_split(X, y,test_size=.5,random_state =123)
clf = LazyClassifier(verbose=0,ignore_warnings=True, custom_metric=None)
models,predictions = clf.fit(X_train, X_test, y_train, y_test)
models

tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/481 [00:00<?, ?B/s]

 97%|█████████▋| 30/31 [17:55<00:05,  5.13s/it]

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002840 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 10865
[LightGBM] [Info] Number of data points in the train set: 6200, number of used features: 73
[LightGBM] [Info] Start training from score -3.495863
[LightGBM] [Info] Start training from score -3.495863
[LightGBM] [Info] Start training from score -3.517369
[LightGBM] [Info] Start training from score -3.539348
[LightGBM] [Info] Start training from score -3.561821
[LightGBM] [Info] Start training from score -3.544919
[LightGBM] [Info] Start training from score -3.596506
[LightGBM] [Info] Start training from score -3.561821
[LightGBM] [Info] Start training from score -3.469614
[LightGBM] [Info] Start training from score -3.556155
[LightGBM] [Info] Start training from score -3.533808
[LightGBM] [Info] Start training from score -3.517369

100%|██████████| 31/31 [18:06<00:00, 35.03s/it]


Accuracy  Balanced Accuracy ROC AUC  F1 Score  \
Model                                                                        
BaggingClassifier                0.98               0.88    None      0.98   
XGBClassifier                    0.98               0.88    None      0.98   
DecisionTreeClassifier           0.97               0.87    None      0.97   
ExtraTreesClassifier             0.90               0.80    None      0.89   
RandomForestClassifier           0.83               0.75    None      0.83   
LogisticRegression               0.50               0.45    None      0.48   
LinearDiscriminantAnalysis       0.46               0.41    None      0.43   
ExtraTreeClassifier              0.43               0.39    None      0.43   
LinearSVC                        0.42               0.38    None      0.38   
SVC                              0.38               0.34    None      0.35   
CalibratedClassifierCV           0.36               0.32    None      0.28   
SGDClassifier                    0.35               0.31    None      0.35   
Perceptron                       0.27               0.24    None      0.27   
NearestCentroid                  0.27               0.24    None      0.26   
BernoulliNB                      0.26               0.23    None      0.23   
PassiveAggressiveClassifier      0.24               0.22    None      0.24   
RidgeClassifierCV                0.18               0.16    None      0.12   
RidgeClassifier                  0.18               0.16    None      0.12   
KNeighborsClassifier             0.16               0.14    None      0.16   
LabelSpreading                   0.15               0.14    None      0.16   
LabelPropagation                 0.15               0.14    None      0.16   
GaussianNB                       0.14               0.12    None      0.08   
LGBMClassifier                   0.11               0.10    None      0.09   
AdaBoostClassifier               0.05               0.05    None      0.03   
DummyClassifier                  0.03               0.03    None      0.00   

                             Time Taken  
Model                                    
BaggingClassifier                  1.65  
XGBClassifier                     11.29  
DecisionTreeClassifier             0.40  
ExtraTreesClassifier               2.91  
RandomForestClassifier             3.60  
LogisticRegression                 2.04  
LinearDiscriminantAnalysis         0.73  
ExtraTreeClassifier                0.11  
LinearSVC                        187.69  
SVC                               13.23  
CalibratedClassifierCV           829.22  
SGDClassifier                      3.16  
Perceptron                         1.38  
NearestCentroid                    0.17  
BernoulliNB                        0.10  
PassiveAggressiveClassifier        2.00  
RidgeClassifierCV                  0.28  
RidgeClassifier                    0.14  
KNeighborsClassifier               0.78  
LabelSpreading                     8.75  
LabelPropagation                   3.59  
GaussianNB                         0.21  
LGBMClassifier                    10.14  
AdaBoostClassifier                 1.73  
DummyClassifier                    0.07

In [ ]:
# for distilbert the accuracy
X = getTrainSetDistilBERT() #Change this to get training set based on word embeddings method.
y = dataset['Target']
X_train, X_test, y_train, y_test = train_test_split(X, y,test_size=.5,random_state =123)
clf = LazyClassifier(verbose=0,ignore_warnings=True, custom_metric=None)
models,predictions = clf.fit(X_train, X_test, y_train, y_test)
models

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/483 [00:00<?, ?B/s]

 97%|█████████▋| 30/31 [13:50<00:04,  4.37s/it]

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004178 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 11429
[LightGBM] [Info] Number of data points in the train set: 6200, number of used features: 76
[LightGBM] [Info] Start training from score -3.495863
[LightGBM] [Info] Start training from score -3.495863
[LightGBM] [Info] Start training from score -3.517369
[LightGBM] [Info] Start training from score -3.539348
[LightGBM] [Info] Start training from score -3.561821
[LightGBM] [Info] Start training from score -3.544919
[LightGBM] [Info] Start training from score -3.596506
[LightGBM] [Info] Start training from score -3.561821
[LightGBM] [Info] Start training from score -3.469614
[LightGBM] [Info] Start training from score -3.556155
[LightGBM] [Info] Start training from score -3.533808
[LightGBM] [Info] Start training from score -3.517369

100%|██████████| 31/31 [14:01<00:00, 27.15s/it]


Accuracy  Balanced Accuracy ROC AUC  F1 Score  \
Model                                                                        
XGBClassifier                    0.98               0.88    None      0.98   
BaggingClassifier                0.98               0.87    None      0.98   
DecisionTreeClassifier           0.97               0.87    None      0.97   
ExtraTreesClassifier             0.85               0.76    None      0.85   
RandomForestClassifier           0.82               0.74    None      0.81   
LogisticRegression               0.54               0.48    None      0.53   
LinearSVC                        0.49               0.44    None      0.46   
ExtraTreeClassifier              0.47               0.42    None      0.47   
LinearDiscriminantAnalysis       0.46               0.41    None      0.45   
CalibratedClassifierCV           0.45               0.40    None      0.39   
SVC                              0.41               0.37    None      0.40   
SGDClassifier                    0.41               0.36    None      0.41   
BernoulliNB                      0.33               0.30    None      0.31   
PassiveAggressiveClassifier      0.33               0.30    None      0.34   
Perceptron                       0.33               0.29    None      0.33   
NearestCentroid                  0.30               0.27    None      0.29   
RidgeClassifierCV                0.26               0.24    None      0.21   
RidgeClassifier                  0.26               0.24    None      0.21   
KNeighborsClassifier             0.18               0.16    None      0.18   
LabelSpreading                   0.16               0.14    None      0.16   
LabelPropagation                 0.16               0.14    None      0.16   
LGBMClassifier                   0.16               0.14    None      0.15   
GaussianNB                       0.12               0.11    None      0.06   
AdaBoostClassifier               0.06               0.05    None      0.03   
DummyClassifier                  0.03               0.03    None      0.00   

                             Time Taken  
Model                                    
XGBClassifier                      7.91  
BaggingClassifier                  1.62  
DecisionTreeClassifier             0.40  
ExtraTreesClassifier               2.10  
RandomForestClassifier             4.60  
LogisticRegression                 1.61  
LinearSVC                        155.89  
ExtraTreeClassifier                0.12  
LinearDiscriminantAnalysis         0.48  
CalibratedClassifierCV           620.73  
SVC                               12.66  
SGDClassifier                      3.81  
BernoulliNB                        0.09  
PassiveAggressiveClassifier        1.40  
Perceptron                         1.16  
NearestCentroid                    0.09  
RidgeClassifierCV                  0.23  
RidgeClassifier                    0.15  
KNeighborsClassifier               0.79  
LabelSpreading                     8.31  
LabelPropagation                   3.37  
LGBMClassifier                    11.63  
GaussianNB                         0.19  
AdaBoostClassifier                 1.76  
DummyClassifier                    0.07

In [ ]:
models[["Accuracy","F1 Score"]][:10]

Accuracy  F1 Score
Model                                         
XGBClassifier                   0.98      0.98
BaggingClassifier               0.98      0.98
DecisionTreeClassifier          0.97      0.97
ExtraTreesClassifier            0.85      0.85
RandomForestClassifier          0.82      0.81
LogisticRegression              0.54      0.53
LinearSVC                       0.49      0.46
ExtraTreeClassifier             0.47      0.47
LinearDiscriminantAnalysis      0.46      0.45
CalibratedClassifierCV          0.45      0.39

In [ ]:
result = pd.DataFrame(columns=["Fold","Model","Accuracy","F1-Score"], index=np.arange(300))
fold = KFold(n_splits=10, random_state=6666, shuffle=True)
X = getTrainSetDistilBERT() #Change this to get training set based on word embeddings method.
y = dataset['Target']
counter = 0
foldcounter = 1
for train_index, test_index in fold.split(X, y):
        print("Processing Fold "+ str(foldcounter) + " ...")
        X_train, X_test, y_train, y_test = \
            X[ X.index.isin(train_index)], X[ X.index.isin(test_index)], y[train_index], y[test_index]
        clf = LazyClassifier(verbose=0,ignore_warnings=True, custom_metric=None)
        models,predictions = clf.fit(X_train, X_test, y_train, y_test)
        for model in models[:].iterrows():
            result.loc[counter]["Fold"] = foldcounter
            result.loc[counter]["Model"] = model[0]
            result.loc[counter]["Accuracy"] = round(model[1][0],3)
            result.loc[counter]["F1-Score"] = round(model[1][3],3)
            counter += 1
        foldcounter += 1
result

Processing Fold 1 ...


 97%|█████████▋| 30/31 [31:01<00:07,  7.81s/it]

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004932 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 12413
[LightGBM] [Info] Number of data points in the train set: 11160, number of used features: 82
[LightGBM] [Info] Start training from score -3.514956
[LightGBM] [Info] Start training from score -3.514956
[LightGBM] [Info] Start training from score -3.517973
[LightGBM] [Info] Start training from score -3.500008
[LightGBM] [Info] Start training from score -3.536266
[LightGBM] [Info] Start training from score -3.511949
[LightGBM] [Info] Start training from score -3.530131
[LightGBM] [Info] Start training from score -3.502980
[LightGBM] [Info] Start training from score -3.524033
[LightGBM] [Info] Start training from score -3.517973
[LightGBM] [Info] Start training from score -3.517973
[LightGBM] [Info] Start training from score -3.50596

100%|██████████| 31/31 [31:14<00:00, 60.48s/it]


Processing Fold 2 ...


...

 97%|█████████▋| 30/31 [31:26<00:08,  8.58s/it]

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.006202 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 12469
[LightGBM] [Info] Number of data points in the train set: 11161, number of used features: 82
[LightGBM] [Info] Start training from score -3.506050
[LightGBM] [Info] Start training from score -3.506050
[LightGBM] [Info] Start training from score -3.521088
[LightGBM] [Info] Start training from score -3.536356
[LightGBM] [Info] Start training from score -3.527167
[LightGBM] [Info] Start training from score -3.536356
[LightGBM] [Info] Start training from score -3.554990
[LightGBM] [Info] Start training from score -3.567608
[LightGBM] [Info] Start training from score -3.491235
[LightGBM] [Info] Start training from score -3.503070
[LightGBM] [Info] Start training from score -3.539437
[LightGBM] [Info] Start training from score -3.52412

100%|██████████| 31/31 [31:40<00:00, 61.32s/it]


Fold                   Model Accuracy F1-Score
0      1           XGBClassifier     0.99     0.99
1      1       BaggingClassifier     0.98     0.98
2      1  DecisionTreeClassifier     0.98     0.98
3      1    ExtraTreesClassifier     0.89     0.89
4      1  RandomForestClassifier     0.87     0.86
..   ...                     ...      ...      ...
295  NaN                     NaN      NaN      NaN
296  NaN                     NaN      NaN      NaN
297  NaN                     NaN      NaN      NaN
298  NaN                     NaN      NaN      NaN
299  NaN                     NaN      NaN      NaN

[300 rows x 4 columns]

Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.


In [ ]:
# for bert the accuracy
X = getTrainSetBERT() #Change this to get training set based on word embeddings method.
y = dataset['Target']
X_train, X_test, y_train, y_test = train_test_split(X, y,test_size=.5,random_state =123)
clf = LazyClassifier(verbose=0,ignore_warnings=True, custom_metric=None)
models,predictions = clf.fit(X_train, X_test, y_train, y_test)
models

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

 97%|█████████▋| 30/31 [14:57<00:04,  4.83s/it]

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002637 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 11429
[LightGBM] [Info] Number of data points in the train set: 6200, number of used features: 76
[LightGBM] [Info] Start training from score -3.495863
[LightGBM] [Info] Start training from score -3.495863
[LightGBM] [Info] Start training from score -3.517369
[LightGBM] [Info] Start training from score -3.539348
[LightGBM] [Info] Start training from score -3.561821
[LightGBM] [Info] Start training from score -3.544919
[LightGBM] [Info] Start training from score -3.596506
[LightGBM] [Info] Start training from score -3.561821
[LightGBM] [Info] Start training from score -3.469614
[LightGBM] [Info] Start training from score -3.556155
[LightGBM] [Info] Start training from score -3.533808
[LightGBM] [Info] Start training from score -3.517369

100%|██████████| 31/31 [15:07<00:00, 29.29s/it]


Accuracy  Balanced Accuracy ROC AUC  F1 Score  \
Model                                                                        
XGBClassifier                    0.98               0.88    None      0.98   
BaggingClassifier                0.98               0.87    None      0.98   
DecisionTreeClassifier           0.97               0.87    None      0.97   
ExtraTreesClassifier             0.85               0.76    None      0.85   
RandomForestClassifier           0.82               0.74    None      0.81   
LogisticRegression               0.54               0.48    None      0.53   
LinearSVC                        0.49               0.44    None      0.46   
ExtraTreeClassifier              0.47               0.42    None      0.47   
LinearDiscriminantAnalysis       0.46               0.41    None      0.45   
CalibratedClassifierCV           0.45               0.40    None      0.39   
SVC                              0.41               0.37    None      0.40   
SGDClassifier                    0.41               0.36    None      0.41   
BernoulliNB                      0.33               0.30    None      0.31   
PassiveAggressiveClassifier      0.33               0.30    None      0.34   
Perceptron                       0.33               0.29    None      0.33   
NearestCentroid                  0.30               0.27    None      0.29   
RidgeClassifierCV                0.26               0.24    None      0.21   
RidgeClassifier                  0.26               0.24    None      0.21   
KNeighborsClassifier             0.18               0.16    None      0.18   
LabelSpreading                   0.16               0.14    None      0.16   
LabelPropagation                 0.16               0.14    None      0.16   
LGBMClassifier                   0.16               0.14    None      0.15   
GaussianNB                       0.12               0.11    None      0.06   
AdaBoostClassifier               0.06               0.05    None      0.03   
DummyClassifier                  0.03               0.03    None      0.00   

                             Time Taken  
Model                                    
XGBClassifier                     11.48  
BaggingClassifier                  2.30  
DecisionTreeClassifier             0.32  
ExtraTreesClassifier               3.19  
RandomForestClassifier             3.38  
LogisticRegression                 3.09  
LinearSVC                        181.43  
ExtraTreeClassifier                0.12  
LinearDiscriminantAnalysis         0.68  
CalibratedClassifierCV           657.38  
SVC                               12.26  
SGDClassifier                      3.59  
BernoulliNB                        0.18  
PassiveAggressiveClassifier        1.75  
Perceptron                         0.86  
NearestCentroid                    0.10  
RidgeClassifierCV                  0.27  
RidgeClassifier                    0.16  
KNeighborsClassifier               1.34  
LabelSpreading                     6.92  
LabelPropagation                   3.70  
LGBMClassifier                    10.63  
GaussianNB                         0.25  
AdaBoostClassifier                 2.01  
DummyClassifier                    0.07

In [ ]:
models[["Accuracy","F1 Score"]][:10]

In [ ]:
result = result.dropna()

In [ ]:
result.to_excel("Resultdistilbert_domain.xlsx")

In [ ]:
pip install tensorflow

In [ ]:
import pandas as pd
import numpy as np
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.model_selection import KFold
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Embedding
from tensorflow.keras.preprocessing.sequence import pad_sequences

# Preparing the DataFrame to store results
result = pd.DataFrame(columns=["Fold", "Model", "Accuracy", "Precision", "Recall", "F1-Score"], index=np.arange(300))
fold = KFold(n_splits=10, random_state=6666, shuffle=True)

# Assuming X is preprocessed sequence data, and y is the target labels
X = getTrainSetALBERT()  # Replace with your sequence data processing
y = dataset['Target'].values
counter = 0
foldcounter = 1

# Define lists to store each metric for mean calculation
accuracy_list = []
precision_list = []
recall_list = []
f1_score_list = []

# Define maximum sequence length for padding
max_sequence_length = 100  # Set appropriate length based on your data

# LSTM model function
def create_rnn_model(input_length, vocab_size):
    model = Sequential([
        Embedding(input_dim=vocab_size + 1, output_dim=128, input_length=input_length),
        LSTM(64, return_sequences=True),
        LSTM(32),
        Dense(1, activation='sigmoid')
    ])
    model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
    return model

# Find the maximum word index in your data
max_word_index = 0
for seq in X:
    # Ensure all elements in the sequence are integers
    seq_int = [int(x) for x in seq if str(x).isdigit()]  # Convert to string first for safety
    if seq_int:  # Check if seq_int is not empty
        max_word_index = max(max_word_index, max(seq_int))

# Iterate over X_test as well to capture words not present in X_train!
for seq in X_test:
    # Ensure all elements in the sequence are integers
    seq_int = [int(x) for x in seq if str(x).isdigit()]  # Convert to string first for safety
    if seq_int:  # Check if seq_int is not empty
        max_word_index = max(max_word_index, max(seq_int))

# Add 1 to max_word_index to account for the 0 index and any potential unseen words during testing.
# Adding a buffer to the vocabulary size.
max_word_index += 50 #previously it was +1

# Cross-validation loop
for train_index, test_index in fold.split(X, y):
    print("Processing Fold "+ str(foldcounter) + " ...")

    # Split data into train and test sets for the current fold
    X_train, X_test = X.iloc[train_index], X.iloc[test_index]
    y_train, y_test = y[train_index], y[test_index]

    # Convert X_train and X_test to lists of lists
    X_train = X_train.values.tolist()  # Convert DataFrame to list of lists
    X_test = X_test.values.tolist()  # Convert DataFrame to list of lists

    # Padding sequences to ensure consistent input shape
    X_train_padded = pad_sequences(X_train, maxlen=max_sequence_length)
    X_test_padded = pad_sequences(X_test, maxlen=max_sequence_length)

    # Create and train the model and passing vacabulary size
    model = create_rnn_model(input_length=max_sequence_length, vocab_size=max_word_index)
    model.fit(X_train_padded, y_train, epochs=50, batch_size=256, verbose=0)

    # Make predictions on the test set
    y_pred = (model.predict(X_test_padded) > 0.5).astype("int32").flatten()

    # Calculate metrics
    accuracy = accuracy_score(y_test, y_pred)
    precision = precision_score(y_test, y_pred, average='weighted')
    recall = recall_score(y_test, y_pred, average='weighted')
    f1 = f1_score(y_test, y_pred, average='weighted')

    # Store metrics in lists for mean calculation
    accuracy_list.append(accuracy)
    precision_list.append(precision)
    recall_list.append(recall)
    f1_score_list.append(f1)

    # Store the results in DataFrame
    result.loc[counter, "Fold"] = foldcounter
    result.loc[counter, "Model"] = "LSTM"
    result.loc[counter, "Accuracy"] = round(accuracy, 3)
    result.loc[counter, "Precision"] = round(precision, 3)
    result.loc[counter, "Recall"] = round(recall, 3)
    result.loc[counter, "F1-Score"] = round(f1, 3)

    counter += 1
    foldcounter += 1

# Calculate mean values
mean_accuracy = np.mean(accuracy_list)
mean_precision = np.mean(precision_list)
mean_recall = np.mean(recall_list)
mean_f1_score = np.mean(f1_score_list)

print(f"Mean Accuracy: {mean_accuracy:.3f}")
print(f"Mean Precision: {mean_precision:.3f}")
print(f"Mean Recall: {mean_recall:.3f}")
print(f"Mean F1-Score: {mean_f1_score:.3f}")


Processing Fold 1 ...
39/39 ━━━━━━━━━━━━━━━━━━━━ 2s 49ms/step
Processing Fold 2 ...
39/39 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step
Processing Fold 3 ...
39/39 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step
Processing Fold 4 ...
39/39 ━━━━━━━━━━━━━━━━━━━━ 2s 46ms/step
Processing Fold 5 ...
39/39 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step
Processing Fold 6 ...
39/39 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step
Processing Fold 7 ...
39/39 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step
Processing Fold 8 ...
39/39 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step
Processing Fold 9 ...
39/39 ━━━━━━━━━━━━━━━━━━━━ 2s 32ms/step
Processing Fold 10 ...
39/39 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step
Mean Accuracy: 0.029
Mean Precision: 0.001
Mean Recall: 0.029
Mean F1-Score: 0.002
